<a href="https://colab.research.google.com/github/xcollantes/stock-quant-frontend/blob/main/algorithm_131.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# @title Imports

import altair as alt
import pandas as pd
import yfinance as yf
import requests
import json
from io import StringIO

from IPython.display import display

FMG_KEY: str = "6fc03c9a2f6330be1eff2950bf3e6f0c"
FINNHUB_KEY: str = "cj4q79pr01qq6hgdo9lgcj4q79pr01qq6hgdo9m0"

In [2]:
# @title Get all company symbols data

us_df = pd.read_csv(
    "https://raw.githubusercontent.com/xcollantes/stock_analysis_dataset/main/us_tickers.csv")

In [3]:
# @title Get day's top drops from FinancialModel

def get_top_losing(percent_threshold: float) -> pd.DataFrame:
  """Return stocks with largest drops from open to close price.

  Args:
    percent_threshold: Percent drop or greater to filter symbols.

  Returns:
    DataFrame of symbol, name, change, price, changesPercentage, exchange,
    exchangeShortName.
  """
  response: requests.Response = requests.get(
      f"https://financialmodelingprep.com/api/v3/stock_market/losers?apikey={FMG_KEY}")
  response_df = pd.json_normalize(response.json())
  return response_df[response_df["changesPercentage"] < percent_threshold * -100]

res_df: pd.DataFrame = get_top_losing(0.10)
res_df = res_df.sort_values(by=["changesPercentage"], ascending=True,
                            ignore_index=True)

In [4]:
# @title Merge company data with largest drop data

def dict_check(check, key) -> any:
  try:
    return check[key]
  except KeyError:
    return None

def get_yahoo_info(symbol: str):
  ticker = yf.Ticker(symbol)
  return (dict_check(ticker.info, "marketCap"),
          dict_check(ticker.info, "volume"),
          dict_check(ticker.info, "fiftyTwoWeekLow"),
          dict_check(ticker.info, "fiftyTwoWeekHigh"))

# Left table is a static dataset; Right table is FinancialModelPrep
joined_df: pd.DataFrame = res_df.merge(
    us_df[["symbol", "exchange", "exchangeShortName",
    "type", "sector", "industry", "description", "website"]],
    how="left",
    on="symbol")

# Append data from Yahoo Finance
yahoo_intermediary_df = pd.DataFrame({
    "MarketCap": [],
    "Volume": [],
    "52WeekLow": [],
    "52WeekHigh": []})
for symbol in joined_df["symbol"]:
  info = get_yahoo_info(symbol)
  yahoo_intermediary_df.loc[len(yahoo_intermediary_df)] = [
      info[0],
      info[1],
      info[2],
      info[3]]

# Join series to main DataFrame
joined_df = pd.concat([joined_df, yahoo_intermediary_df], axis=1)

In [5]:
# @title Filter high drop companies

security_type = "stock" # @param ["", 'stock', 'etf', 'trust'] {allow-input: true}
sector = "Technology" # @param ["", 'Basic Materials', 'Communication Services', 'Consumer Cyclical', 'Consumer Defensive', 'Financial Services', 'Healthcare', 'Industrials', 'Technology'] {allow-input: true}
industry = "" # @param ["", 'Aerospace & Defense', 'Agricultural Inputs', 'Auto & Truck Dealerships', 'Biotechnology', 'Communication Equipment', 'Computer Hardware', 'Drug Manufacturers—Specialty & Generic', 'Electronic Gaming & Multimedia', 'Farm Products', 'Gambling', 'Health Information Services', 'Medical Devices', 'Medical Instruments & Supplies', 'Other Industrial Metals & Mining', 'Packaging & Containers', 'Pharmaceutical Retailers', 'Shell Companies', 'Software—Application', 'Software—Infrastructure', 'Solar', 'Specialty Industrial Machinery', 'Specialty Retail', 'Trucking'] {allow-input: true}

# Get df filtered by industry and sector and capitalization
# TODO: Options
if security_type:
  filtered_df = joined_df[joined_df["type"] == security_type]

if sector:
  filtered_df = joined_df[joined_df["sector"] == sector]

if industry:
  filtered_df = joined_df[joined_df["industry"] == industry]

filtered_df = filtered_df.rename(columns={
    "symbol": "Symbol",
    "name": "Name",
    "change": "DayChange",
    "price": "ClosingPrice",
    "changesPercentage": "PercentDayChange",
    "exchange": "Exchange",
    "exchangeShortName": "ExchangeShortName",
    "sector": "Sector",
    "industry": "Industry",
    "description": "Description",
    "type": "Type",
    "website": "Website"})

filtered_df = filtered_df.reset_index(drop=True)

show_drops_df = filtered_df[["Symbol", "Name", "PercentDayChange", "52WeekLow",
                             "ClosingPrice", "52WeekHigh", "MarketCap",
                             "Volume", "Sector", "Industry", "Type",
                             "Exchange"]]
show_drops_df.style \
    .format(formatter={"PercentDayChange": "{:.1f}%",
                       "52WeekLow": "${:.2f}",
                       "ClosingPrice": "${:.2f}",
                       "52WeekHigh": "${:.2f}",
                       "MarketCap": "${:,.2f}", "Volume": "{:,.0f}"}) \
    .background_gradient(subset=["PercentDayChange"], cmap="autumn") \
    .background_gradient(subset=["MarketCap"], cmap="Greens") \
    .highlight_null(color="gray")

In [6]:
# @title Compare closing prices with other drops

# TODO: Does not count weekends
duration_ago = "1year" # @param ["3days", "10days", "1month", "2months", "3months", "6months", "1year", "2year"]

days_convert = {
      "3days": 3,
      "10days": 10,
      "1month": 30,
      "2months": 60,
      "3months": 90,
      "6months": 180,
      "1year": 365,
      "2year": 730
    }

days_ago: int = days_convert[duration_ago]


def clean_symbols_many(user_in: str) -> list[str]:
  """Parse user input for many stock symbols and return list of symbols."""
  if user_in == "":
    return [""]

  split_in: list[str] = user_in.split(",")
  return [ x.strip().upper() for x in split_in if x.strip() != "" ]


def get_symbol_data(ticker_symbol: str, days_ago: int) -> pd.DataFrame:
  """Given a date range, returns historical price range.

  Args:
    ticker_symbol: String of ticker.
    days_ago: Range of stock history prior to today.

  Returns:
    Historical data.
  """
  df: pd.DataFrame = yf.Ticker(ticker_symbol.upper())
  history = df.history(period=f"{days_ago}d")
  history["DateCloseET"] = history.index  # Add non-index field
  return history


def multiple_symbols_chart(symbol_data: pd.DataFrame, title: str = "") -> alt.Chart:
  """Show multi-line graph for a many stock symbols.

  Column names must match the source data from Yahoo Finance historical prices.

  Args:
    symbol_data: DataFrame with Close, DateCloseET, Symbol, Name,
    Percent Change.
    title: Optional chart title header.

  Returns:
    Altair graph.
  """
  chart_width: int = 1500
  x_axis = alt.X("DateCloseET", axis=alt.Axis(labelAngle=-50), title="Dates")
  y_axis = alt.Y("PercentChange", title="Percent change", axis=alt.Axis(labelExpr="datum.value * 100 + '%'"))

  color = alt.Color("Name:N")
  selection = alt.selection_multi(fields=["Name"], bind="legend", on="mouseover", toggle="event.ctrlKey")
  selection_opacity = alt.condition(selection, alt.value(1), alt.value(0.09))
  tooltip = [alt.Tooltip("Name:N"),
             alt.Tooltip("Symbol:N"),
             alt.Tooltip("Sector:N"),
             alt.Tooltip("Industry:N"),
             alt.Tooltip("PercentChange:Q", format=".2%"),
             alt.Tooltip("DateCloseET:T"),
             alt.Tooltip("Close", format="$.2f")]
  point = alt.OverlayMarkDef(filled=False, fill="white")

  change_chart = alt.Chart(symbol_data).mark_line(point=point).encode(
      x=x_axis,
      y=y_axis,
      color=color,
      tooltip=tooltip,
      opacity=selection_opacity
  ).properties(
    title={"text": "Biggest drops", "subtitle": "Hold SHIFT to select multiple in Legend"},
    height=500,
    width=chart_width,
    # selection=alt.selection_multi(fields=[""], )
  ).add_selection(selection).interactive()

  dollar_chart = alt.Chart(symbol_data).mark_line(point=point).encode(
      x=x_axis,
      y=alt.Y("Close", title="Closing price", axis=alt.Axis(labelExpr="'$' + datum.value")),
      color=color,
      tooltip=tooltip,
      opacity=selection_opacity
  ).properties(
    height=200,
    width=chart_width,
  ).add_selection(selection).interactive()

  return alt.vconcat(change_chart, dollar_chart).configure_axis(
    labelFontSize=18,
    titleFontSize=18
  ).configure_legend(
      labelFontSize=15,
      titleFontSize=12
  ).configure_title(
      fontSize=20
  ).configure_point(
    size=200)


agg_graph_df = pd.DataFrame()

for index, row in filtered_df.iterrows():
  symbol = row["Symbol"]
  name = row["Name"]

  hist_symbol_df = get_symbol_data(symbol, days_ago)

  # Add columns from company data
  hist_symbol_df["Symbol"] = symbol
  hist_merged_df = hist_symbol_df.merge(filtered_df, how="left",
                                        left_on=["Symbol"], right_on=["Symbol"])

  # Aggregate the historical prices for each symbol in one DataFrame
  agg_graph_df = pd.concat([agg_graph_df, hist_merged_df])

# Index is originally date
agg_graph_df = agg_graph_df.reset_index(drop=True)

# Add percent change column
sorted_df = agg_graph_df.sort_values(["Symbol", "DateCloseET"]).reset_index(
    drop=True)

pct_change_series: pd.Series = sorted_df.groupby(
    "Symbol", group_keys=False, sort=False)["Close"].apply(
        lambda x: x.pct_change())

# Add column with percent changes
sorted_df["PercentChange"] = pct_change_series

# sorted_df = sorted_df.rename(columns={"name": "Name",
#                                       "sector": "Sector",
#                                       "industry": "Industry",
#                                       "description": "Description",
#                                       "type": "Type",
#                                       "website": "Website"})

In [36]:
filtered_df

Symbol                         Name  DayChange  ClosingPrice  \
0    RBT   Rubicon Technologies, Inc.    -0.6100        1.0200   
1   FTNT               Fortinet, Inc.   -18.9900       56.7700   
2   DOCN  DigitalOcean Holdings, Inc.   -11.5700       35.1100   
3   SONM     Sonim Technologies, Inc.    -0.1791        0.5510   
4   RBCN     Rubicon Technology, Inc.    -0.2800        1.2000   
5   KSPN        Kaspien Holdings Inc.    -0.0235        0.1355   
6    NIR      Near Intelligence, Inc.    -0.1600        0.9800   
7    JFU                      9F Inc.    -0.6493        4.0407   
8     SQ                  Block, Inc.   -10.0300       63.5200   

   PercentDayChange                 Exchange ExchangeShortName   Type  \
0          -37.4233  New York Stock Exchange              NYSE  stock   
1          -25.0660     NASDAQ Global Select            NASDAQ  stock   
2          -24.7858  New York Stock Exchange              NYSE  stock   
3          -24.5309    NASDAQ Capital Market            NASDAQ  stock   
4          -18.9189    NASDAQ Capital Market            NASDAQ  stock   
5          -14.7799    NASDAQ Capital Market            NASDAQ  stock   
6          -14.0351     NASDAQ Global Market            NASDAQ  stock   
7          -13.8444     NASDAQ Global Market            NASDAQ  stock   
8          -13.6370  New York Stock Exchange              NYSE  stock   

       Sector                             Industry  \
0  Technology                 Software—Application   
1  Technology              Software—Infrastructure   
2  Technology              Software—Infrastructure   
3  Technology              Communication Equipment   
4  Technology  Semiconductor Equipment & Materials   
5  Technology                 Software—Application   
6  Technology                 Software—Application   
7  Technology      Information Technology Services   
8  Technology              Software—Infrastructure   

                                         Description  \
0  Rubicon Technologies, Inc., a digital marketpl...   
1  Fortinet, Inc. provides cybersecurity and netw...   
2  DigitalOcean Holdings, Inc., through its subsi...   
3  Sonim Technologies, Inc. provides ruggedized m...   
4  Rubicon Technology, Inc. provides monocrystall...   
5  Kaspien Holdings Inc. operates an e-commerce s...   
6  Near Intelligence, Inc. operates as a cloud-ba...   
7  9F Inc., together with its subsidiaries, opera...   
8  Block, Inc., together with its subsidiaries, c...   

                             Website     MarketCap      Volume  52WeekLow  \
0                                NaN  1.952504e+08  10950158.0      0.251   
1           https://www.fortinet.com  4.457558e+10  32793826.0     42.610   
2       https://www.digitalocean.com  3.110746e+09  10719043.0     23.375   
3                                NaN  2.258847e+07   1915255.0      0.400   
4  https://www.rubicontechnology.com  2.892312e+06      7652.0      1.150   
5                                NaN  6.727570e+05      9940.0      0.126   
6                                NaN  4.976626e+07    789245.0      0.980   
7                                NaN  4.757237e+07      3956.0      1.490   
8                                NaN  3.842299e+10  33382491.0     51.340   

   52WeekHigh  
0      7.9400  
1     81.2400  
2     53.8800  
3      1.3000  
4     17.7400  
5      7.0499  
6     18.6500  
7     14.9200  
8     93.1900

In [ ]:
# @title Add description

def get_desc(desc, symbol: str):

  text = alt.Chart({"values": [{}]}).mark_text().encode(
      x=alt.value(300),
      y=alt.value(100),
      text=alt.value([desc])
  )
  box = alt.Chart({'values':[{}]}).mark_rect(cornerRadius=4).encode(
      x=alt.value(800),
      x2=alt.value(400),
      y=alt.value(200),
      y2=alt.value(200 + 200)
  )
  return alt.layer(box, text)

d = filtered_df[filtered_df["Symbol"] == "NIR"]["Description"]
print(d.values)
get_desc(d.values[0], "NIR")

In [73]:
# @title Traditional stock chart


def filter_by_symbol(agg_stock_df: pd.DataFrame, symbol: str) -> pd.DataFrame:
  return agg_stock_df[agg_stock_df["Symbol"] == symbol]


def stock_chart_trad_mult(symbol_data: pd.DataFrame, height: int, title: str = "") -> alt.Chart:
  """Show multi-line graph for a many stock symbols.

  Column names must match the source data from Yahoo Finance historical prices.

  Args:
    symbol_data: DataFrame with Close, DateCloseET, Symbol, Name,
    Percent Change.
    title: Optional chart title header.

  Returns:
    Altair graph.
  """
  chart_width: int = 800
  x_axis = alt.X("DateCloseET", axis=alt.Axis(labelAngle=-50))
  y_axis = alt.Y("Close", scale=alt.Scale(
      domain=[symbol_data["Close"].min(),
              symbol_data["Close"].max()]), title="Close price")

  color = alt.Color("Name:N", legend=None)
  selection = alt.selection_multi(
        fields=["DateCloseET"],
        nearest=True,
        on="mouseover",
        empty="none",
        clear="mouseout"
      )
  selection_opacity = alt.condition(selection, alt.value(1), alt.value(0))

  tooltip = [alt.Tooltip("Name:N"),
            #  alt.Tooltip("Symbol:N"),
            #  alt.Tooltip("Sector:N"),
            #  alt.Tooltip("Industry:N"),
             alt.Tooltip("PercentChange:Q", format=".2%"),
             alt.Tooltip("DateCloseET:T"),
             alt.Tooltip("Close", format="$.2f")]

  change_chart = alt.Chart(symbol_data).mark_line().encode(
      x=x_axis,
      y=y_axis,
      color=color,
      tooltip=tooltip,
  ).properties(
    title={"text": title, "subtitle": f"{title}"},
    height=height,
    width=chart_width,
    # selection=alt.selection_multi(fields=[""], )
  )

  horiz = alt.Chart(symbol_data).mark_rule(strokeWidth=2, color="red").encode(
        x=x_axis,
        opacity=selection_opacity,
        tooltip=tooltip,
  ).add_selection(selection)

  return alt.layer(change_chart, horiz)

chart = alt.vconcat().configure_axis(
    labelFontSize=18,
    titleFontSize=18
  ).configure_title(
      fontSize=20
  )


def get_earnings_surprises_yahoo(symbol: str, limit: int = 8) -> pd.DataFrame:
  """Return DataFrame with earnings dates and results.

  Also returns next 4 earnings calls.
  """
  ticker = yf.Ticker(symbol)
  earning_df = ticker.get_earnings_dates(limit=limit).rename(columns={
    "EPS Estimate": "EstimatedEarning",
    "Reported EPS": "ActualEarning",
    "Surprise(%)": "SurprisePercent",
  })
  earning_df["Date"] = earning_df.index
  return earning_df.reset_index(drop=True)


def get_earnings_surprises_fmp(symbol: str) -> pd.DataFrame:
  url = f"https://financialmodelingprep.com/api/v3/earnings-surprises/{symbol}?apikey={FMG_KEY}"
  response = requests.Response = requests.get(url)
  return pd.json_normalize(response.json())


def earnings_beat_chart(earnings_df: pd.DataFrame, height: int, symbol_name: str = ""):
  point_size: int = 200
  stroke_size: int = 4
  date_filter: str = "year(datum.Date) > year(now()) - 5"

  if symbol_name != "":
    symbol_name = f"({symbol_name})"

  x_axis = alt.X("Date:T")
  tooltip = alt.Tooltip(["Date:T", "EstimatedEarning:Q",
                         "ActualEarning:Q"])

  expected_chart = alt.Chart(earnings_df).mark_point(
      size=point_size, strokeWidth=stroke_size, color="gray").encode(
      x=x_axis,
      y=alt.Y("EstimatedEarning:Q", axis=alt.Axis(labels=False)),
      tooltip=tooltip,
  ).transform_filter(date_filter).properties(title=f"Earnings beat quarterly {symbol_name}",
               height=height,
               width=500)

  actual_chart = alt.Chart(earnings_df).mark_point(
      size=point_size, strokeWidth=stroke_size, color="green").encode(
      x=x_axis,
      y=alt.Y("ActualEarning:Q", axis=alt.Axis(labels=False)),
      tooltip=tooltip,
  ).transform_filter(date_filter)

  return (expected_chart + actual_chart)


height_per_symbol: int = 200

for symbol in sorted_df["Symbol"].unique():
  earnings_beat_df: pd.DataFrame = get_earnings_surprises_yahoo(symbol, limit=10)
  chart &= (
      alt.layer(stock_chart_trad_mult(filter_by_symbol(sorted_df, symbol),
                            height_per_symbol, symbol),
      earnings_beat_chart(earnings_beat_df, height_per_symbol, symbol)))

chart

alt.VConcatChart(...)

In [ ]:
# @title Save for browser view

chart.save("chart.html")

In [ ]:
# @title Show drop percentage progression

multiple_symbols_chart(sorted_df)

In [ ]:
# @title Get competitors to compare with each company with a large drop

def get_competitors(symbol: str) -> pd.Series:
  """Get list of peers of a given company.

  Args:
    symbol: One stock symbol for a company.

  Returns:
    List of competitor company stock symbols in a Series.
  """
  response: requests.Response = requests.get(
      f"https://finnhub.io/api/v1/stock/peers?symbol={symbol}&token={FINNHUB_KEY}")
  return pd.Series(json.loads(response.content))

peers_series = get_competitors("NET")

In [ ]:
peers_series

In [ ]:
# For each symbol:
#   Get trend line
#   Get fundamentals compared to competitors



In [ ]:
# @title Show earnings hit or miss
# @markdown Limited financialmodelingprep.com (250/day)
choose_symbol = "GOOG" #@param {type:"string"}

def get_earnings_surprises(symbol: str) -> pd.DataFrame:
  url = f"https://financialmodelingprep.com/api/v3/earnings-surprises/{symbol}?apikey={FMG_KEY}"
  response = requests.Response = requests.get(url)
  return pd.json_normalize(response.json())


def earnings_beat_chart(earnings_df: pd.DataFrame, symbol_name: str = ""):
  date_filter: str = "year(datum.date) > year(now()) - 5"

  if symbol_name != "":
    symbol_name = f"({symbol_name})"

  expected_chart = alt.Chart(earnings_df).mark_point(
      size=1000, strokeWidth=7, color="gray").encode(
      x=alt.X("date:T"),
      y=alt.Y("estimatedEarning:Q"),
      tooltip=alt.Tooltip(["date:T", "estimatedEarning:Q",
                           "actualEarningResult:Q"]),
  ).transform_filter(date_filter).properties(title=f"Earnings beat quarterly {symbol_name}",
               height=500,
               width=1100)

  actual_chart = alt.Chart(earnings_df).mark_point(
      size=1000, strokeWidth=7, color="green").encode(
      x=alt.X("date:T"),
      y=alt.Y("actualEarningResult:Q"),
      tooltip=alt.Tooltip(["date:T", "estimatedEarning:Q",
                           "actualEarningResult:Q"]),
  ).transform_filter(date_filter)

  return (expected_chart + actual_chart).configure_axis(
    labelFontSize=18,
    titleFontSize=18
  ).configure_legend(
      labelFontSize=15,
      titleFontSize=12
  ).configure_title(
      fontSize=20
  ).configure_point(
    size=200)


earnings_beat_df: pd.DataFrame = get_earnings_surprises(choose_symbol)
earnings_beat_chart(earnings_beat_df, choose_symbol)